In [1]:
import sys
sys.path.append("..")

In [2]:
from datasets.loader import get_imdb_dataloaders

In [3]:
import torch
torch.cuda.empty_cache()
device = "cpu"

In [4]:
train, test = get_imdb_dataloaders(1000, 4, device, root_dir="../.data")

In [5]:
from network.ctransformer import CTransformer

In [6]:
import torch
import torch.nn.functional as F

In [7]:
model = CTransformer(64, 2, 2, 32, 1000, 2, device)

In [8]:
opt = torch.optim.Adam(lr=3e-4, params=model.parameters())
sch = torch.optim.lr_scheduler.LambdaLR(opt, lambda i: min(i / (10000 / 32), 1.0))

# training loop
seen = 0
for e in range(40):

    print(f"\n epoch {e}")
    model.train(True)

    for batch in train:

        opt.zero_grad()

        input = batch.text[0]
        label = batch.label - 1

        if input.size(1) > 32:
            input = input[:, :32]
        out = model(input)
        loss = F.nll_loss(out, label)

        loss.backward()

        # clip gradients
        # - If the total gradient vector has a length > 1, we clip it back down to 1.
        torch.nn.utils.clip_grad_norm_(model.parameters(), 1.0)

        opt.step()
        sch.step()

        seen += input.size(0)
        print("classification/train-loss", float(loss.item()), seen)

    with torch.no_grad():

        model.train(False)
        tot, cor = 0.0, 0.0

        for batch in test:

            input = batch.text[0]
            label = batch.label - 1

            if input.size(1) > 32:
                input = input[:, :32]
            out = model(input).argmax(dim=1)

            tot += float(input.size(0))
            cor += float((label == out).sum().item())

        acc = cor / tot
        print(f"-- validation accuracy {acc:.3}")
        print("classification/test-loss", float(loss.item()), e)



 epoch 0
classification/train-loss 0.6906893253326416 4
classification/train-loss 0.6178321838378906 8
classification/train-loss 0.7112587094306946 12
classification/train-loss 0.7298486232757568 16
classification/train-loss 0.6590962409973145 20
classification/train-loss 0.71893310546875 24
classification/train-loss 0.6945119500160217 28
classification/train-loss 0.6687251329421997 32
classification/train-loss 0.7255147695541382 36
classification/train-loss 0.6276511549949646 40
classification/train-loss 0.639790952205658 44
classification/train-loss 0.7283068895339966 48
classification/train-loss 0.6874452233314514 52
classification/train-loss 0.6745748519897461 56
classification/train-loss 0.7514840960502625 60
classification/train-loss 0.6826932430267334 64
classification/train-loss 0.6582688689231873 68
classification/train-loss 0.68979811668396 72
classification/train-loss 0.6672678589820862 76
classification/train-loss 0.7029095888137817 80
classification/train-loss 0.661780238

KeyboardInterrupt: 